# Doc2vec tutorial

The basic idea is: act as if a document has another floating word-like vector, which contributes to all training predictions, and is updated like other word-vectors, but we will call it a doc-vector. Gensim’s Doc2Vec class implements this algorithm.



In [1]:
import os
import gensim

In [2]:
# Set file names for train and test data
test_data_dir = os.path.join(gensim.__path__[0], 'test', 'test_data')
lee_train_file = os.path.join(test_data_dir, 'lee_background.cor')
lee_test_file = os.path.join(test_data_dir, 'lee.cor')

In [3]:
import smart_open

def read_corpus(fname, tokens_only=False):
    with smart_open.open(fname, encoding="iso-8859-1") as f:
        for i, line in enumerate(f):
            tokens = gensim.utils.simple_preprocess(line)
            if tokens_only:
                yield tokens
            else:
                # For training data, add tags
                yield gensim.models.doc2vec.TaggedDocument(tokens, [i])

train_corpus = list(read_corpus(lee_train_file))
test_corpus = list(read_corpus(lee_test_file, tokens_only=True))

In [13]:
import pandas as pd
pd.DataFrame(train_corpus)

words   tags
0    [hundreds, of, people, have, been, forced, to,...    [0]
1    [indian, security, forces, have, shot, dead, e...    [1]
2    [the, national, road, toll, for, the, christma...    [2]
3    [argentina, political, and, economic, crisis, ...    [3]
4    [six, midwives, have, been, suspended, at, wol...    [4]
..                                                 ...    ...
295  [team, of, australian, and, israeli, scientist...  [295]
296  [today, is, world, aids, day, and, the, latest...  [296]
297  [the, federal, national, party, has, rejected,...  [297]
298  [university, of, canberra, academic, proposal,...  [298]
299  [australia, will, take, on, france, in, the, d...  [299]

[300 rows x 2 columns]

## Training the Model

In [15]:
model = gensim.models.doc2vec.Doc2Vec(vector_size=50, min_count=2, epochs=40)

In [17]:
model.build_vocab(train_corpus)

In [20]:
print(f"word 'penalty' appeared {model.wv.get_vecattr('penalty', 'count')} times in the training corpus")

word 'penalty' appeared 4 times in the training corpus


In [22]:
model.train(train_corpus, total_examples=model.corpus_count, epochs=model.epochs)

In [25]:
vector = model.infer_vector(['only'])
print(vector)

[-0.29854172 -0.0444538  -0.11895405  0.02514958 -0.12772763 -0.18277678
  0.02528828  0.13904344 -0.2368442  -0.16329834  0.07805561 -0.19971043
  0.00434327 -0.0243273  -0.13427772  0.00684696  0.20506294  0.06715514
 -0.02257395 -0.15633327  0.09492309  0.07911702  0.1220558  -0.02221537
  0.15232928  0.02313896 -0.26606715  0.12367363 -0.13409242 -0.15018721
  0.12660739 -0.04537873 -0.10081073  0.10679985 -0.00419924  0.11344568
  0.12908879 -0.09622322 -0.0274845   0.10321381  0.06208762 -0.00683388
 -0.10797358  0.04688664  0.1194722  -0.00422846  0.13539341 -0.02065336
  0.05821449 -0.00671344]


# Graph2Vec

In [148]:
import os
import json
import glob
import hashlib
import pandas as pd
import networkx as nx
from tqdm import tqdm
from joblib import Parallel, delayed
# from param_parser import parameter_parser
from gensim.models.doc2vec import Doc2Vec, TaggedDocument

In [28]:
!ls dataset/

ClaimFake_combined.csv		       NewsFake_combined.csv
ClaimFake_tweets_combined.csv	       NewsFake_tweets_combined.csv
ClaimFake_tweets_replies_combined.csv  NewsFake_tweets_replies_combined.csv
ClaimReal_combined.csv		       NewsReal_combined.csv
ClaimReal_tweets_combined.csv	       NewsReal_tweets_combined.csv
ClaimReal_tweets_replies_combined.csv  NewsReal_tweets_replies_combined.csv


In [30]:
DATAPATH = 'dataset/'

## Dataload

In [51]:
from glob import glob
EdgeList = glob(DATAPATH+'*replies_combined.csv')

In [57]:
Genuine1 = pd.read_csv(EdgeList[0])
Genuine2 = pd.read_csv(EdgeList[2])

Fake1 = pd.read_csv(EdgeList[1])
Fake2 = pd.read_csv(EdgeList[3])

In [62]:
Genuine = pd.concat([Genuine1,Genuine2])
Fake = pd.concat([Fake1, Fake2])

## Graph2vec

In [107]:
FakeBox = [f'graph{i}' for i in range(Fake['news_id'].nunique())]
GenuineBox = [f'graph{i}' for i in range(Genuine['news_id'].nunique())]

In [108]:
for i in range(Fake.news_id.nunique()):
    FakeBox[i] = nx.from_pandas_edgelist(Fake[Fake['news_id'] == list(set(Fake.news_id))[i]], 'tweet_id', 'reply_id', create_using=nx.DiGraph())

In [137]:
for i in range(Genuine.news_id.nunique()):
    GenuineBox[i] = nx.from_pandas_edgelist(Genuine[Genuine['news_id'] == list(set(Genuine.news_id))[i]], 'tweet_id', 'reply_id', create_using=nx.DiGraph())

## tips

In [138]:
features = nx.degree(GenuineBox[0])
# features = {int(k): v for k, v in features.items()} wrong code
features = {int(k) : v for k , v in dict(features).items()} ## modified code

## Feature extraction

### practice code

In [244]:
new_features ={}
for node in GenuineBox[0].nodes:
#     print(node)
    features = nx.degree(GenuineBox[0])
    features = {int(k) : v for k , v in dict(features).items()}
    extracted_features = [str(v) for k, v in dict(features).items()] ##
    nebs = GenuineBox[0].neighbors(node)
    degs = [features[neb] for neb in nebs]
    features = [str(features[node])] + sorted([str(deg) for deg in degs])
    features = "_".join(features)
    hash_object = hashlib.md5(features.encode())
    hashing = hash_object.hexdigest()
    new_features[node] = hashing

In [245]:
features = extracted_features + list(new_features.values())
doc1 = gensim.models.doc2vec.TaggedDocument(features, tags=["graph1"])

### utilizing code

In [343]:
from tqdm import tqdm
doc = [f'graph{i}' for i in range(len(GenuineBox))]

for j in tqdm(range(len(GenuineBox))):
    new_features ={}
    for node in GenuineBox[j].nodes:
    #     print(node)
        features = nx.degree(GenuineBox[j])
        features = {int(k) : v for k , v in dict(features).items()}
        extracted_features = [str(v) for k, v in dict(features).items()] ##
        nebs = GenuineBox[j].neighbors(node)
        degs = [features[neb] for neb in nebs]
        features = [str(features[node])] + sorted([str(deg) for deg in degs])
        features = "_".join(features)
        hash_object = hashlib.md5(features.encode())
        hashing = hash_object.hexdigest()
        new_features[node] = hashing
    features = extracted_features + list(new_features.values())
    doc[j] = gensim.models.doc2vec.TaggedDocument(features, tags=[Genuine['news_id'].unique()[j]])

100%|██████████| 1244/1244 [01:25<00:00, 14.51it/s] 


In [344]:
doc_fake = [f'graph{i}' for i in range(len(FakeBox))]

for j in tqdm(range(len(FakeBox))):
    new_features ={}
    for node in FakeBox[j].nodes:
    #     print(node)
        features = nx.degree(FakeBox[j])
        features = {int(k) : v for k , v in dict(features).items()}
        extracted_features = [str(v) for k, v in dict(features).items()] ##
        nebs = FakeBox[j].neighbors(node)
        degs = [features[neb] for neb in nebs]
        features = [str(features[node])] + sorted([str(deg) for deg in degs])
        features = "_".join(features)
        hash_object = hashlib.md5(features.encode())
        hashing = hash_object.hexdigest()
        new_features[node] = hashing
    features = extracted_features + list(new_features.values())
    doc_fake[j] = gensim.models.doc2vec.TaggedDocument(features, tags=[Fake['news_id'].unique()[j]])

100%|██████████| 113/113 [00:03<00:00, 36.81it/s]


In [415]:
import pickle
with open(r'doc_fake.pickle','wb') as f:
    pickle.dump(doc_fake, f)
    
with open(r'doc_genuine.pickle','wb') as ff:
    pickle.dump(doc, ff)

## Doc2vec training

In [345]:
DIMENSION= int(128)
MINCOUNT = int(5)
SAMPLE = int(0.0001)
WORKERS = int(4)
EPOCHS = int(10)
LEARNINGRATE = int(0.025)

model = Doc2Vec(doc,
               vector_size=DIMENSION,
               window=0,
               min_count=MINCOUNT,
               dm=0,
               sample=SAMPLE,
               workers=WORKERS,
               epochs=EPOCHS,
               alpha=LEARNINGRATE)

In [346]:
model_fake = Doc2Vec(doc_fake,
               vector_size=DIMENSION,
               window=0,
               min_count=MINCOUNT,
               dm=0,
               sample=SAMPLE,
               workers=WORKERS,
               epochs=EPOCHS,
               alpha=LEARNINGRATE)

## model save

In [347]:
from gensim.test.utils import get_tmpfile

fname = get_tmpfile('Genuine_doc2vec_model')

model.save(fname)
model = Doc2Vec.load(fname)

fname2 = get_tmpfile('Fake_doc2vec_model')


model_fake.save(fname2)
model_fake = Doc2Vec.load(fname2)

## vectored graph

In [349]:
Genuine['news_id'].unique()

array([100000, 100001, 100011, ...,   4224,   4236,   4311])

In [350]:
model.dv[4311]

array([ 0.00108734, -0.00157959, -0.00504846,  0.0132201 , -0.0040369 ,
       -0.00046798, -0.00934575,  0.01120756,  0.01321421,  0.00934729,
        0.00908764, -0.00672009, -0.00342732, -0.00841816,  0.00645114,
        0.0120613 , -0.00111653,  0.00529016, -0.01146591, -0.00649232,
       -0.00774654, -0.01048854, -0.0090675 , -0.00186334,  0.0007187 ,
       -0.00747072,  0.00218505,  0.00316125,  0.00384517,  0.00601297,
        0.00577128, -0.0005433 , -0.01432397, -0.00397049, -0.00713243,
       -0.00546208, -0.00444103,  0.01886758, -0.01045541, -0.00019747,
       -0.01177106, -0.00743936, -0.0101192 , -0.00798218, -0.00220249,
       -0.00571642, -0.00687343,  0.00863541,  0.00581986,  0.00689616,
        0.00278837, -0.00458693,  0.00649188, -0.00949594,  0.00114065,
        0.00319302,  0.00203413, -0.00165875,  0.00074845,  0.00231274,
       -0.00102487,  0.00305733,  0.01460689, -0.01353247,  0.00047366,
        0.00652626, -0.00737739, -0.01294545, -0.0091968 , -0.00

In [278]:
Fake['news_id'].unique()

array([    17,     26,     38,     46,     51,     55,     65,     67,
           68,     73,     84,    115,    124,    199,    200,    201,
          203,    206,    253,    263,    297,    307,    310,    327,
          366,    374,    404,    406,    417,    418,    443,    466,
          483,    485,    496,    508,    517,    528,    536,    545,
          548,    556,    558,    561,    562,    565,    570,    577,
          587,    590,    593,    602,    606,    610,    633,    637,
          643,    645,    646,    650,    654,    658,    664,    666,
          671,    685,    686,    691,    696,    701,    715,    718,
          719,    725,    733,    740,    753,    754,    758,    765,
          771,    783,    784,    792,    795,    812,    819,    836,
          840,    842,    857,    859,    860,    862,    880,    891,
          900,    903,    912,    968, 100001, 100003, 100004, 100005,
       100007, 100008, 100011, 100012, 100013, 100015, 100019, 100022,
      

In [352]:
model_fake.dv[17]

array([ 7.5491169e-03, -4.4647544e-03,  2.0022714e-03,  4.5670103e-03,
       -6.0008159e-03,  2.5553682e-03,  5.9511373e-04,  9.4434032e-03,
        6.8712314e-03,  4.5867828e-03, -1.2416677e-03, -1.1539072e-03,
        8.2280440e-03, -6.2610302e-03,  8.1995770e-04, -2.5788483e-03,
        5.1575592e-03,  4.2695506e-04, -5.4166825e-03, -5.3257612e-03,
        1.9771969e-03, -5.6017092e-03,  1.6770056e-03, -6.4103445e-04,
        7.9840478e-03, -4.3998505e-03,  5.4581752e-03, -7.5544519e-03,
       -9.5183905e-03, -5.0397944e-03, -7.4340682e-03, -2.9390911e-03,
       -8.1855049e-03,  4.2075231e-03, -7.1860142e-03,  2.1377893e-03,
       -2.1985653e-03,  5.5174707e-03,  5.3669070e-03, -7.0733898e-03,
        6.7234929e-03, -7.9917079e-03, -4.4506728e-03,  4.0243110e-03,
       -3.2759691e-03, -1.2150644e-03,  8.6648855e-03,  5.1346878e-03,
        3.4283425e-03,  5.0538699e-03, -7.9333559e-03,  3.4081119e-03,
        2.5535710e-03,  8.9608191e-04, -1.5937502e-03,  1.3119493e-03,
      

## concat features

In [284]:
!ls dataset

ClaimFake_combined.csv		       NewsFake_combined.csv
ClaimFake_tweets_combined.csv	       NewsFake_tweets_combined.csv
ClaimFake_tweets_replies_combined.csv  NewsFake_tweets_replies_combined.csv
ClaimReal_combined.csv		       NewsReal_combined.csv
ClaimReal_tweets_combined.csv	       NewsReal_tweets_combined.csv
ClaimReal_tweets_replies_combined.csv  NewsReal_tweets_replies_combined.csv


In [299]:
!ls

0804_graphClassificationTutorial.ipynb	GraphConstruction.ipynb
Btest.csv				logs
CoAID					newsFakeEmbedding.csv
DataPreprocessing.ipynb			newsFakeOneHot.csv
dataset					newsFakePre.csv
dataset2				newsRealEmbedding.csv
dataset3				newsRealOneHot.csv
dataset4				newsRealPre.csv
diff_tags.png				trial_0810.ipynb
embedding.ipynb				trialbox
fakeGraphBox.pickle			Untitled1.ipynb
genuineGraphBox.pickle			Untitled2.ipynb
graph2vec				Untitled.ipynb
Graph2Vec.ipynb				usefulPackges.ipynb


In [358]:
TEST = pd.read_csv('newsRealEmbedding.csv')

In [357]:
model.dv[1]

array([ 2.0384972e-03, -6.1499751e-03,  3.0659370e-03,  1.2937100e-03,
       -4.6722568e-04,  4.7459649e-03, -3.7611159e-03, -1.1721238e-03,
        9.9220313e-04,  2.4622323e-03, -6.6551776e-03, -3.9988887e-03,
        6.2765828e-03,  5.9550343e-04,  3.2310367e-03, -6.9350842e-03,
       -1.6758547e-03,  1.7594893e-03,  1.8775963e-03,  6.8928548e-03,
        5.9193153e-05, -3.9021957e-03, -2.8487872e-03,  7.2905258e-03,
        6.0731093e-03, -6.9378414e-03, -2.8875740e-03,  4.1458574e-03,
        7.9658540e-04,  6.9480971e-03, -4.4521485e-03, -2.6476081e-03,
        6.2295757e-03,  4.1947900e-03,  6.6457279e-03, -2.6755738e-03,
        1.7273568e-03, -4.9554743e-03, -5.0033228e-03, -4.4500064e-03,
       -6.6946601e-03, -1.7944676e-03,  2.6442430e-03, -1.6199722e-03,
        2.4783546e-03,  3.9575123e-03,  5.7111559e-03,  2.2175761e-03,
        6.3099125e-03, -2.8396789e-03, -3.5871577e-03, -8.7955361e-04,
        4.6067140e-03,  3.5267470e-03, -6.5193712e-03, -2.1690296e-03,
      

In [361]:
TEST.newsid.sample(1)

1567    10012
Name: newsid, dtype: int64

In [403]:
len(set(TEST.newsid))

4529

In [407]:
TEST['newsid'].nunique()

4529

In [412]:
display(len(doc_fake))
display(len(TEST))

113

4529

In [408]:
for i in range(TEST['newsid'].nunique()):
    print(model.dv[TEST.newsid[i]])

[-4.3944041e-03 -6.4103338e-03 -8.0602663e-03  8.9225164e-03
  2.1807533e-03 -1.2079128e-03 -1.2011531e-02 -2.3468477e-03
 -5.2304659e-03  3.9745476e-03  4.3736156e-03  3.3461519e-03
 -1.7972993e-03 -4.0156944e-03  1.8569948e-03 -2.3825616e-03
 -1.0016139e-04  7.9705603e-03 -9.0906881e-03 -3.5925519e-03
 -5.1425514e-03 -7.7832234e-04 -7.9925284e-03 -7.9401286e-04
  7.4866032e-03 -6.2696645e-03 -7.4315355e-03 -9.0862382e-03
  5.1588947e-03 -5.8250776e-03  6.2078107e-03  2.3869877e-03
 -9.2601851e-03 -4.3257638e-03 -3.1573558e-03 -1.3563908e-03
 -2.1300761e-03 -1.6581799e-03 -7.4522276e-03  3.5024860e-03
 -3.9774682e-03 -6.4992914e-03  1.6811820e-03 -1.1042036e-02
  3.8778663e-03 -3.7445014e-03 -9.0614421e-04  1.3194737e-03
  5.8240988e-03 -2.8186385e-03  1.7881162e-04  4.0606689e-04
 -5.0532599e-03 -7.3736422e-03 -2.0440326e-03  8.4586022e-03
  2.5012894e-03  8.3803042e-04 -1.7567923e-03  1.0234739e-02
  7.4836462e-05  7.9855258e-03  8.5270647e-03 -6.5091457e-03
  3.7532435e-03 -2.68417

[-4.8857261e-03  5.3873360e-03 -1.7183343e-03 -1.0617863e-04
 -3.3222840e-04 -1.9719142e-03 -1.1189510e-03 -2.3415308e-03
 -3.0798153e-03  6.9472496e-03 -6.7891981e-03  7.6862401e-03
  2.2485983e-03  9.3174423e-04  3.0819986e-03 -6.4347875e-03
 -4.9960869e-03  1.8855140e-03 -1.5571562e-03  7.5705480e-03
 -7.2212587e-03  5.5474597e-03  6.9749607e-03  4.3446193e-03
  2.4815553e-03 -1.8930804e-03  6.1806380e-03 -1.8854793e-03
  1.2092983e-03  7.6779001e-03  2.7264266e-03 -6.7831593e-04
 -2.5906179e-03 -5.8621317e-03 -3.8093622e-03  6.6184984e-03
 -7.0221932e-03  1.5178093e-03 -4.5988680e-04 -2.1407993e-03
  1.1928838e-03 -6.6567102e-04  4.9719270e-03  2.6730066e-03
 -8.3920307e-04 -1.7032111e-03  5.2245805e-04 -3.9033098e-03
  1.7013913e-03  6.7087263e-03  2.2780471e-03 -7.3588458e-03
  3.1948145e-03 -7.6673790e-03 -5.4809181e-03  2.0883412e-03
  7.1802987e-03 -6.3402145e-03  6.1813025e-03 -1.6716893e-03
  2.6142464e-03  3.3227180e-03 -8.4910731e-05 -2.9662864e-03
 -2.3234354e-03 -4.18030

[-6.1254199e-03  2.9986396e-03  5.1488806e-03  9.4046758e-04
 -2.7015901e-03  5.3122686e-03  5.7638396e-04 -2.7487190e-03
 -7.4940477e-03  7.5501343e-03 -6.2148469e-03  5.2075689e-03
  7.8378050e-03  3.4257786e-03  4.2004171e-03 -2.5088470e-03
  5.3744721e-03  1.8732657e-03 -3.8836297e-04  7.4207583e-03
 -5.0790170e-03 -5.9443116e-03  2.8196460e-04 -5.3925486e-03
  5.8806792e-04  4.3709282e-04  1.2849770e-03  6.7556510e-03
 -4.8574110e-04 -7.6854313e-03 -5.9911744e-03 -6.4462693e-03
  2.1541875e-03  7.0449691e-03  4.7084878e-04 -7.2953440e-03
  4.7339713e-03 -3.6658531e-03 -5.3648144e-04  7.5852438e-03
  5.1514627e-03  6.9916835e-03  4.1415226e-03 -5.0578499e-03
 -1.4093110e-03 -4.6059024e-03  6.2366845e-03  7.1109585e-03
 -4.1170465e-03  7.3205931e-03 -5.9810067e-03 -4.7592213e-04
 -4.1883015e-03  3.6838290e-03 -6.2347720e-03 -4.1920156e-03
  7.4921837e-03  9.8348595e-04 -3.7703977e-03 -4.0005911e-03
 -7.9309633e-03 -6.3687999e-04  5.3647365e-03  9.9273992e-04
 -7.5695193e-03  5.89555

[ 2.9521454e-03  3.9510503e-03  7.8003034e-03  1.3339296e-03
 -2.5681034e-04  2.9719081e-03  4.3959748e-03 -1.4438648e-03
  6.1848871e-03  7.4743498e-03  5.0423127e-03 -5.5908151e-03
  7.1163271e-03 -3.1447783e-03 -2.7171168e-03 -5.2579697e-03
 -7.8066625e-03  6.7610592e-03 -3.8109720e-04 -3.6882497e-03
 -1.4583431e-03  5.3889677e-04  2.0162072e-03  7.4221548e-03
  6.1473437e-03 -9.1642328e-04 -5.6879409e-03 -5.3545423e-03
 -6.9251284e-05  2.0910334e-03  4.3302961e-03 -3.8518328e-03
  3.3116676e-03  6.2744506e-03 -3.7995633e-03 -9.7223744e-04
  1.8145777e-03  6.0093850e-03  3.2844003e-03  7.1504470e-03
 -5.3570028e-03  4.4205841e-03 -6.8010464e-03  3.6791358e-03
 -6.1465073e-03 -1.3204906e-03 -7.5651538e-03  3.4922548e-03
 -6.7614019e-07  3.5598986e-03  1.8259343e-03 -6.3956995e-03
 -3.5326239e-03  4.6867803e-03  5.7934560e-03 -3.7877951e-03
  6.9757421e-03 -7.7304319e-03 -6.9158562e-03  7.7642091e-03
  4.5064297e-03  5.8423150e-03  4.6369601e-03  1.2522656e-03
  2.4533756e-03 -2.67332

[-4.1757245e-03 -6.6146553e-03 -6.7635868e-03  2.9077306e-03
  4.6482496e-03  2.7984343e-03 -7.5971205e-03  6.0130041e-03
  5.3690262e-03 -7.2044991e-03  3.7368052e-03  3.3222418e-03
  3.0685943e-03  3.0395128e-03  5.8827717e-03 -3.7345961e-03
  7.1743317e-03 -7.1006417e-03 -5.1969700e-03  5.7016052e-03
 -7.0481114e-03  4.4288263e-03  8.6049922e-04 -5.0555374e-03
 -1.9635875e-03  6.0591977e-03 -2.9343423e-03 -5.1000640e-03
 -3.2621529e-03  5.6153163e-04  5.0013382e-03  2.1358766e-04
  5.7135932e-03 -3.3787712e-03 -2.1713842e-03 -5.7421904e-03
 -6.4984187e-03 -3.0284747e-04  7.3669329e-03 -2.3821741e-03
  3.9913245e-03  5.7547055e-03  2.9449724e-04 -3.1675715e-03
 -7.3856395e-03  6.0595907e-03 -5.4392125e-03 -6.9866516e-03
  1.1406783e-03 -4.0029567e-03  4.6295896e-03 -2.3083035e-03
  2.7559083e-03 -6.6703688e-03  4.5196023e-03 -7.5461995e-03
 -1.5854463e-03 -4.0695798e-03 -5.6977756e-04 -4.8460793e-03
  3.7238598e-03  3.3995453e-03  4.4110827e-03 -2.7245730e-03
  4.1563064e-04  7.35459

...

[ 1.9115284e-03 -7.2137490e-03 -1.0889787e-03  6.7951158e-03
  4.2503756e-03  3.4461897e-03  7.9758465e-06  6.5976288e-03
 -5.8051515e-03 -1.4362819e-03  5.6934711e-03  3.3241659e-03
 -7.7741221e-04  5.4641627e-03 -6.2201321e-03 -5.8929194e-03
  7.5034257e-03 -3.4132376e-03  2.6796684e-03 -6.2788967e-03
  3.8144253e-03 -7.0921928e-03  5.6573488e-03 -6.3165016e-03
  5.9930868e-03  2.6733987e-04  7.0427526e-03 -6.4922255e-03
  1.0513794e-03 -5.0886683e-03  7.7539235e-03  5.7592653e-03
 -6.2303469e-03 -1.7453283e-03  3.9822012e-03  1.8520355e-03
  4.8362724e-03  2.5237426e-03 -8.5942447e-06 -5.0388444e-03
  7.0566945e-03 -5.1616523e-03 -4.0583480e-03 -3.0439720e-03
  4.4986904e-03  2.9021762e-03 -1.8021576e-03  7.4027348e-03
  4.0043723e-03 -3.5704300e-03  3.3224560e-04  2.1473374e-03
 -2.4751853e-03 -5.3498242e-03 -6.9122128e-03 -5.0237644e-03
 -2.9262397e-03 -3.6116373e-03 -5.4746978e-03 -5.5794697e-03
 -4.3890439e-03 -2.0439737e-04  6.1633103e-03 -4.0543191e-03
  5.9120357e-06 -2.17938

[-4.1107405e-03 -2.4354160e-03  1.5019774e-03  4.2207539e-03
  6.3273497e-04  9.3737990e-04  1.0731816e-04 -2.2212621e-03
  7.4237958e-04 -1.6122870e-03 -4.7141202e-03  6.6299178e-04
  5.6507066e-03 -2.9767025e-03  8.3882548e-04 -4.4812374e-03
  4.7656521e-03 -3.2860432e-03  1.3416260e-04 -1.4871769e-03
  7.2135031e-03  3.5480019e-03 -3.6505274e-03  1.5865862e-03
 -4.4077449e-04 -5.3667501e-03  3.3642203e-03 -6.7180190e-03
 -6.9574900e-03 -6.2769260e-03 -2.9185880e-03  3.4059044e-03
  6.5720361e-03  4.3414198e-03  4.6831779e-03  3.0800551e-03
 -4.7977809e-03 -7.4175689e-03 -3.9673038e-04  2.0827949e-03
 -4.4740736e-03  5.2677970e-03  7.5143389e-03 -7.7931322e-03
  6.8740826e-03  4.4427309e-03  3.9358623e-03 -2.9113442e-03
  6.5474957e-04 -1.6372595e-03  7.2918907e-03 -4.9218759e-03
  4.4569783e-03 -4.1749775e-03 -3.7168823e-03 -5.6475271e-03
 -3.3894852e-03  3.3837557e-04 -4.5961849e-03 -2.4207681e-03
  7.2310548e-03 -5.2640811e-03 -6.0467497e-03  3.2310467e-03
 -6.0517713e-04 -7.54929

[ 5.5752676e-03 -3.4966916e-03 -7.2854627e-03 -4.1535310e-04
  6.6097733e-03 -1.0207165e-03  6.7650713e-04  1.8609781e-03
  7.4009243e-03  2.7752928e-03 -4.5722332e-03 -3.8585644e-03
 -7.7898484e-03  1.1918694e-04 -3.1919144e-03 -3.6374032e-03
  2.6717409e-04  7.3423292e-03  7.1228966e-03  6.5195281e-03
  1.4106296e-03 -5.9074536e-03 -4.9772933e-03 -6.7290477e-04
 -6.0611852e-03 -8.1826374e-04  7.4799433e-03  1.1802055e-03
  1.9935593e-03  6.4558461e-03 -6.3028038e-03 -5.6422129e-04
 -1.3278760e-03  9.4480254e-04  1.3388656e-03  5.1891431e-04
  8.5701421e-04  4.0999781e-03 -3.7531592e-03  6.3245054e-03
 -6.9192089e-03 -6.0133692e-03 -5.0443206e-03 -5.0343983e-03
  5.6138877e-03 -4.6383776e-04  1.2979247e-03 -1.5351977e-03
  6.9525819e-03  3.8154013e-03 -4.5605283e-03 -2.8288923e-03
 -4.0441342e-03 -9.8597445e-04 -5.5697337e-03  9.9382177e-04
  5.3573679e-03 -6.2647499e-03 -5.8695022e-03  5.3693261e-03
  2.0875409e-03  6.0748104e-03 -1.6353056e-03 -2.2419691e-03
  4.1134879e-03  4.00591

[ 4.52036224e-03  5.47412224e-03  6.67935796e-03 -6.18454441e-03
  7.65843689e-03 -6.27498515e-03 -3.48289683e-03 -7.68707134e-03
  6.85699657e-03  3.33310664e-03 -6.28384389e-03  2.81502493e-03
  6.59607165e-03 -7.27899000e-03  1.19960867e-03  1.38945132e-03
 -1.04779378e-04  6.20741956e-03 -1.47112459e-03 -5.41549735e-03
 -2.03447603e-03  3.95346619e-03 -7.14050233e-03 -3.87239642e-03
  4.48290817e-03  3.53170000e-03 -2.32986361e-03  3.63661163e-03
  3.82863730e-03 -6.79639913e-03  2.94172950e-03 -5.30797057e-03
 -2.39861570e-03 -6.52930699e-03 -3.88988480e-03  4.71029058e-03
  3.71204875e-03  4.86571342e-04 -6.99125417e-03  3.36263329e-04
  7.08978623e-03 -5.14570624e-04 -7.48855993e-04  2.07023695e-04
 -5.71908988e-03 -3.87791917e-03 -1.14163384e-03  3.67364287e-03
 -3.99538130e-03  5.62510639e-03 -2.04009563e-03  7.58893415e-03
  7.09856302e-03 -4.79558483e-04 -2.43071467e-04  5.56270778e-03
  1.17548183e-03 -9.39499587e-05 -4.31734324e-03  6.27559051e-03
 -4.52611782e-03 -3.50880

[-0.00091877  0.00717993  0.00088479 -0.00524526 -0.00551486 -0.00497797
 -0.00457642 -0.00760766  0.00102029 -0.00370557  0.00153965 -0.00096723
  0.00207994  0.00355803  0.00092817 -0.00685537 -0.00025592  0.00335049
 -0.00250555  0.00682789  0.00122816  0.00532707  0.0006439   0.00022983
  0.00414757  0.00543681 -0.00088447 -0.00586227 -0.00267026  0.00587143
 -0.00088976  0.00259141  0.00307445  0.00581441  0.00582615  0.00164519
  0.00719375  0.00678101 -0.00444638  0.00111061  0.00186355 -0.00222361
  0.00153618  0.00043559 -0.00662191 -0.00221087 -0.00411637 -0.000992
  0.00540027 -0.00483756  0.00440761  0.00098848 -0.00619575 -0.00637964
  0.00525935 -0.00672954  0.00437752  0.00589108  0.001459   -0.00181672
  0.00293998  0.00659084  0.00716695 -0.00575963 -0.001497    0.00501031
 -0.00211248 -0.00406836 -0.00521447 -0.0011286  -0.00449985  0.00574684
 -0.00633559 -0.00497659 -0.00503557  0.00193139 -0.00774533  0.00619509
  0.00438285 -0.00630704 -0.00302726  0.00113927 -0.0